In [1]:
import os
import pandas as pd
from tqdm import tqdm
from PIL import Image as Im
from huggingface_hub import notebook_login
from datasets import load_dataset, Dataset, Image

### Load a set with coordinates

In [2]:
data = pd.read_csv('full-gt.csv') # from URL: https://graphics.cs.msu.ru/projects/traffic-sign-recognition.html
data.head()

filename  x_from  y_from  width  height sign_class  \
0  autosave01_02_2012_09_13_33.jpg     649     376     18      18        2_1   
1  autosave01_02_2012_09_13_34.jpg     671     356     20      21        2_1   
2  autosave01_02_2012_09_13_35.jpg     711     332     27      26        2_1   
3  autosave01_02_2012_09_13_36.jpg     764     290     37      36        2_1   
4  autosave01_02_2012_09_13_36.jpg     684     384     17      17       1_23   

   sign_id  
0        0  
1        0  
2        0  
3        0  
4        1

In [3]:
os.listdir('rtsd-frames')[:5] # from URL: https://www.kaggle.com/datasets/watchman/rtsd-dataset

['autosave01_02_2012_09_13_32.jpg',
 'autosave01_02_2012_09_13_33.jpg',
 'autosave01_02_2012_09_13_34.jpg',
 'autosave01_02_2012_09_13_35.jpg',
 'autosave01_02_2012_09_13_36.jpg']

### Saving crop files

In [4]:
source_dir = 'rtsd-frames'
target_dir = 'dataset'

if not os.path.exists(target_dir):
    os.makedirs(target_dir)

def get_sign(
        filename, x_from, y_from, width, height, sign_class, sign_id, 
        img_path=source_dir, res_path=target_dir
    ): 
    img = Im.open(f'{img_path}/{filename}')
    img = img.crop((x_from, y_from, x_from + width, y_from + height))
    filename = f'{sign_class}___{sign_id}__{filename}'
    img.save(f'{target_dir}/{filename}')
    return {'filename': filename,  'sign_class': sign_class, 'sign_id': sign_id}

In [5]:
result, bad_data = [], []
for i in tqdm(range(len(data))):
    try:
        result.append(get_sign(**data.iloc[i].to_dict()))
    except Exception as e:
        bad_data.append((e, data.iloc[i].to_dict()))
        print('.', end='')

100%|██████████████████████████████████████████████████████████████████████████| 104358/104358 [18:08<00:00, 95.90it/s]


In [6]:
len(os.listdir(target_dir))

104358

In [7]:
len(result)

104358

In [8]:
len(bad_data)

0

### Metadata generation

In [9]:
pd.DataFrame(result).to_csv(f'{target_dir}.csv', index=False)

In [10]:
df = pd.DataFrame(result)
df.drop(columns=['sign_id'], inplace=True)
df.columns = ['file_name', 'additional_feature']
df.head()

file_name additional_feature
0   2_1___0__autosave01_02_2012_09_13_33.jpg                2_1
1   2_1___0__autosave01_02_2012_09_13_34.jpg                2_1
2   2_1___0__autosave01_02_2012_09_13_35.jpg                2_1
3   2_1___0__autosave01_02_2012_09_13_36.jpg                2_1
4  1_23___1__autosave01_02_2012_09_13_36.jpg               1_23

In [11]:
df.to_json(f'{target_dir}/metadata.jsonl', orient='records', lines=True); df.head()

file_name additional_feature
0   2_1___0__autosave01_02_2012_09_13_33.jpg                2_1
1   2_1___0__autosave01_02_2012_09_13_34.jpg                2_1
2   2_1___0__autosave01_02_2012_09_13_35.jpg                2_1
3   2_1___0__autosave01_02_2012_09_13_36.jpg                2_1
4  1_23___1__autosave01_02_2012_09_13_36.jpg               1_23

In [12]:
metadata = pd.read_csv(f'{target_dir}.csv') # или metadata = df.copy()
metadata.columns = ['image', 'sign_class', 'sign_id']
metadata['image'] = metadata['image'].apply(lambda x: f'{target_dir}/{x}')
metadata = metadata.to_dict(orient='list')

### Creating a formatted dataset

In [13]:
dataset = Dataset.from_dict(metadata).cast_column("image", Image())

In [14]:
dataset

Dataset({
    features: ['image', 'sign_class', 'sign_id'],
    num_rows: 104358
})

In [15]:
dataset[2]

{'image': <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=27x26 at 0x1EFD1DD5C70>,
 'sign_class': '2_1',
 'sign_id': 0}

In [16]:
dataset[2]['image']

### Uploading to remote storage

In [17]:
notebook_login()

In [18]:
dataset.push_to_hub("eleldar/rtsd_cleaned")